# Neural Networks Automate Feature Engineering

Last time, we noticed that our Logistic Regression model could only create linear decision boundaries, but that manual "feature engineering" such as using a radius could achieve other shapes.

This time, we'll explore how neural networks can be used to build such new features which can then feed into other systems ("downstream tasks") such as logistic regression models. 

Rather than write it all by hand in numpy, we'll use PyTorch. For examples of converting a simple NumPy training code to PyTorch, see the official documentation, ["PyTorch by Examples"](https://pytorch.org/tutorials/beginner/pytorch_with_examples.html).

In [ ]:
import plotly.express as px
import plotly.graph_objects as go
import numpy as np 
import matplotlib.pyplot as plt 
import pandas as pd
from tqdm import tqdm 

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset
from torch import optim
from torch.utils.data import DataLoader

## Define the Data
Make our dataset $(X,Y)$ the same as at the end of the previous lesson:

In [ ]:
np.random.seed(0)
npoints = 300
xs = 2*np.random.rand(npoints) - 1
ys = 2*np.random.rand(npoints) - 1
zs = 2*np.random.rand(npoints) - 1 
X = np.vstack([np.ones(npoints), xs,ys,zs]).T
print(X.shape)

radius = 1
Y = ((X[:,1]**2 + X[:,2]**2 + X[:,3]**2) > radius).astype(np.int16)

(300, 4)


In [ ]:
fig = go.Figure(data=[go.Scatter3d( x=X[:,1], y=X[:,2], z=X[:,3],
    mode='markers', marker=dict(color=Y, size=7))])
fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))  # tight layout
fig.show()

## Split Data into Train/Val subsets

From the previous lesson, we had this routine:

In [ ]:
def train_val_split(X, Y, split_pct=0.8):
    indices = np.arange(X.shape[0])
    np.random.shuffle(indices)
    split_ind = int(split_pct*len(indices))
    indices_train, indices_val = indices[:split_ind], indices[split_ind:]
    X_train, Y_train = X[indices_train,:], Y[indices_train]
    X_val, Y_val = X[indices_val,:], Y[indices_val]
    return X_train, Y_train, X_val, Y_val


X_train, Y_train, X_val, Y_val = train_val_split(X, Y)

## Define the PyTorch Dataset and Dataloader
Our PyTorch `Dataset` class object will be very simple. (For more info, see PyTorch documentation on ["Writing Custom Datasets, Dataloaders AND Transforms"](https://pytorch.org/tutorials/beginner/data_loading_tutorial.html).)

In [ ]:
class ourDataset(Dataset):
    # got this from https://pytorch.org/tutorials/beginner/basics/data_tutorial.html
    def __init__(self, X, Y):
        self.X, self.Y = X, Y 

    def __len__(self):   # required: method to return how many items are in the Dataset
        return self.X.shape[0]

    def __getitem__(self, idx): # serve up a new X_i, Y_i pair
        return torch.Tensor(self.X[idx]), torch.Tensor([self.Y[idx]])

In [ ]:
train_ds = ourDataset(X_train, Y_train)
val_ds = ourDataset(X_val, Y_val)

# a few tests:
print(f"{len(train_ds)} points.")
print("X_train[0],Y_train[0] =",X_train[0],Y_train[0])
print(f"train_ds[0] = {train_ds[0]}")

240 points.
X_train[0],Y_train[0] = [ 1.         -0.7421474  -0.3863798   0.31352392] 0
train_ds[0] = (tensor([ 1.0000, -0.7421, -0.3864,  0.3135]), tensor([0.]))


For the dataloaders we can just call `DataLoader`, and note that it can do its own `shuffle` operation, but that this serves a *different* than the shuffling we did for our train/val split above. 

In [ ]:
batch_size = 32 # can experiment with various batch sizes
train_dl = DataLoader(train_ds, batch_size=batch_size, shuffle=True)
val_dl = DataLoader(val_ds, batch_size=batch_size, shuffle=True)

## Define the Model

Let's grab the final "`Net2`" model code from the end of our "[03_NNsFitCurves](https://colab.research.google.com/drive/11K8e51vPwsVyuAvxlpyTIb65HDkBCJdG#scrollTo=LzgQwGzWr779)" lesson, and add a sigmoid activation for the 1-neuron output (note that there's a better way to do this, which we'll try further down):

In [ ]:
class Net2(nn.Module): 
    # every PyTorch model class needs an __init__() and a forward()
    def __init__(self, 
        hidden_dims=[], # list of how many neurons in each hidden layers[] 
        in_dim=2,   # dimenisions of input 
        out_dim=1): # dimensions of output
        super().__init__()    # you always need this super() call for class inheritance

        self.activation = F.relu    # we'll use ReLU activations internally, but feel free to try others, see "Non-linear activation functions", https://pytorch.org/docs/stable/nn.functional.html
        self.output_activation = torch.sigmoid 

        # below is where we define our layers, thereby "allocating memory" in a sense
        self.layers = nn.ModuleList()                       # special kind of list [] for pytorch layers
        self.layers.append ( nn.Linear(in_dim, hidden_dims[0]) )  # first hidden layer
        for i in range(len(hidden_dims)-1):
            self.layers.append( nn.Linear(hidden_dims[i], hidden_dims[i+1])  )
        self.layers.append( nn.Linear(hidden_dims[-1], out_dim) )

 
    # forward() is where the actual computation is performed, x is the input
    def forward(self, x):           # for our raw, non-fastai-Tabular version
        for i, layer in enumerate(self.layers):
            x = layer(x)
            if i < len(self.layers)-1: 
                x = self.activation(x)    # activation for all layers except the output  
            else:
                x = self.output_activation(x)      
        return x   

In [ ]:
hidden_dims=[10,10,10]  # how many neurons in the hidden layers, 1 output neuron is added to this
torch.manual_seed(0)  # for reproducability 
model = Net2(hidden_dims=hidden_dims, in_dim=X.shape[-1])

Put the model on the GPU if we can: 

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"
print(f"Using {device} device")
model.to(device)

Using cuda device


Net2(
  (layers): ModuleList(
    (0): Linear(in_features=4, out_features=10, bias=True)
    (1): Linear(in_features=10, out_features=10, bias=True)
    (2): Linear(in_features=10, out_features=10, bias=True)
    (3): Linear(in_features=10, out_features=1, bias=True)
  )
)

## Define the Loss and Optimizer

In [ ]:
loss_fn = nn.BCELoss()
lr = 0.002           # learning rate; try different values
optimizer = optim.Adam(model.parameters(), lr=lr)  # "Adam" optimizer is a good general-purpose gradient descent algorithm

## Training Loop: Let's go!

In [ ]:
max_steps = 10000
with tqdm(range(max_steps)) as t: 
     for step in t:
        model.train()
        X_batch, Y_batch = next(iter(train_dl))
        X_batch, Y_batch = X_batch.to(device), Y_batch.to(device) # move to GPU

        optimizer.zero_grad()
        preds = model(X_batch)
        loss = loss_fn(preds, Y_batch)

        # check validation set
        X_val_batch, Y_val_batch = next(iter(val_dl))
        X_val_batch, Y_val_batch = X_val_batch.to(device), Y_val_batch.to(device)
        model.eval()
        preds_val = model(X_val_batch)
        loss_val = loss_fn(preds_val, Y_val_batch)
        # TODO: add accuracy measure

        t.set_description(f"step {step}: loss = {loss.item():.4e}, loss_val = {loss_val.item():.4e}")
        loss.backward()
        optimizer.step()

step 9999: loss = 0.0000, loss_val = 0.0804: 100%|██████████| 10000/10000 [01:15<00:00, 132.08it/s]


## Plot the results

In [ ]:
def plot_points_and_surface(model, X, Y):

    # plot the dots
    XY_all = np.hstack([X, Y[:,np.newaxis]])
    columns = ['ones','x','y','z','class']
    df_all = pd.DataFrame(XY_all, columns=columns)
    fig = px.scatter_3d(df_all, x='x', y='y', z='z', color='class') 

    # plot the predictions over a 3D mesh, showing isosurface for dcision boundary
    iso= True  
    if iso:
        x, y, z = XY_all[:,1], XY_all[:,2], XY_all[:,3]

        # make a 3d mesh of coordinate values to run new predictions on
        XX, YY, ZZ = np.mgrid[x.min():x.max():40j, y.min():y.max():40j, z.min():z.max():40j]
        DD = np.ones(XX.shape)

        # now we need to grab all these values and turn them into inputs "X_vis"
        X_vis = np.vstack([DD.flatten(), XX.flatten(), YY.flatten(), ZZ.flatten()]).T
        print("X_vis.shape =",X_vis.shape)
        X_vis = torch.Tensor(X_vis).to(device)
        model.to(device)
        model.eval()
        preds_3d = model(X_vis).cpu().detach().numpy()

        fig.add_trace(go.Isosurface(       # show values near "0.5" decision boundary
            x=XX.flatten(), y=YY.flatten(), z=ZZ.flatten(), value=preds_3d.flatten(),
            isomin=0.499,  isomax=0.501, opacity=0.5, showscale=False, colorscale='Viridis'))
        fig.add_trace(go.Isosurface(  # see-through volume colored with pred value
            x=XX.flatten(), y=YY.flatten(), z=ZZ.flatten(), value=preds_3d.flatten(),
            isomin=0,  isomax=1,  opacity=0.25, showscale=False, colorscale='Viridis' ))
    fig.update_layout(margin=dict(l=0, r=0, b=0, t=0))  # tight layout
    
    fig.show()
    return fig  

fig = plot_points_and_surface(model, X, Y)

X_vis.shape = (64000, 4)


# Summary of Logistic Regression / Binary Classification 

The following image summarizes our results:

* (top left) two classes of points (separated by radius).
* (top right) Logistic Regression alone on x,y,z, can only draw plane-surface decision boundaries (because it's just a linear combination of coordinates with a sigmoid activation slapped on the end).
* (bottom left) manual "feature engineering" in which we manually compute the radius and use that as an input to the LR algorithm, resulting in a perfectly-spherical decision boundary (but it required manual intervention on our part)
* (bottom right) LR sigmoid but with a 3-layer neural network on the front end.  The neural network does automatic "feature engineering", but only approximates the true decision surface.  And since the activations were all ReLUs, the decision boundary is a 'soccerball-like' piecewise-planar surface


![bc_summary](https://raw.githubusercontent.com/drscotthawley/DLAIE/main/images/bc_summary.png)

# Addendum: Careful Calcs via `BCEWithLogitsLoss`

Rather than putting a final sigmoid on the output and then using `BCELoss`, we can do better by leaving our neural network output as a linear activation...

> **Terminology**: the values produced from such a model are known as "logits" because they are intended as inputs to a logistic sigmoid / or its multidimensional analog known as [`softmax`](https://pytorch.org/docs/stable/generated/torch.nn.Softmax.html).

...and then use PyTorch's [BCEWithLogitsLoss](https://pytorch.org/docs/stable/generated/torch.nn.BCEWithLogitsLoss.html), which will give us a bit more numerical precision. This is akin to the careful calculations described in the **"Appendix: Careful Coding BCE"** in the ["Naughty by Numbers: Classification at Christmas"](https://hedges.belmont.edu/naughty/) webpage. 

If we do this, we need to remember to compute the sigmoid of the output manually whenever we want "true" model predictions.
